In [1]:
"""Import all the relevant libraries."""

from mkd_blockchain import MKDBlockchain
from blockchain_utils import BlockchainUtils
import block
from pubsub import pub
from node import Node
from transaction import Transaction
from sensor_transaction import SensorTransaction
from transaction_pool import TransactionPool
from wallet import Wallet
from Crypto.PublicKey import RSA
import pprint
import random
import time
from cluster import Cluster
from mkdtree import kdtree

In [2]:
"""Initialize Nodes with Genesis Block"""

print('START')
MAX_NODES = 9999
num_nodes = 80
num_clusters = 16
forging_interval = 10  # Time interval.  10 units of time
nodes = [] #list of all nodes
blockchain_dimensions = 4
genesis_node_id = int(num_nodes/2)

#itterate through and initialize each node
then = time.time()
for i in range(num_nodes):
    new_node = Node(i+1, 0)
    #new_node.blockchain = mkd_blockchain
    new_node.start_listener('c0')
    nodes.append(new_node)
now = time.time()-then
print(f'block init time @ {num_nodes} nodes: {now}')

#  initialize each cluster
clusters = []
for i in range(num_clusters):
    new_cluster = Cluster(i+1)
    new_cluster.start_listener(('c' + str(i+1)))
    clusters.append(new_cluster)
    print(f'cluster {new_cluster.cluster_id} initialized')

genesis_forger = nodes[genesis_node_id-1].wallet.public_key_string()
mkd_blockchain = MKDBlockchain(blockchain_dimensions, genesis_node_id, genesis_forger)


publisher = nodes[genesis_node_id-1]

start_broadcast = time.time()
publisher.publish(mkd_blockchain)
completed_broadcast = time.time() - start_broadcast
print(f'time to complete broadcast to {num_nodes} nodes: {completed_broadcast}')


START
block init time @ 80 nodes: 184.86356687545776
cluster 1 initialized
cluster 2 initialized
cluster 3 initialized
cluster 4 initialized
cluster 5 initialized
cluster 6 initialized
cluster 7 initialized
cluster 8 initialized
cluster 9 initialized
cluster 10 initialized
cluster 11 initialized
cluster 12 initialized
cluster 13 initialized
cluster 14 initialized
cluster 15 initialized
cluster 16 initialized
n1 in c0 received MKDBlockchain: <mkd_blockchain.MKDBlockchain object at 0x0000013C9ABCCEE0>
n2 in c0 received MKDBlockchain: <mkd_blockchain.MKDBlockchain object at 0x0000013C9ABCCEE0>
n3 in c0 received MKDBlockchain: <mkd_blockchain.MKDBlockchain object at 0x0000013C9ABCCEE0>
n4 in c0 received MKDBlockchain: <mkd_blockchain.MKDBlockchain object at 0x0000013C9ABCCEE0>
n5 in c0 received MKDBlockchain: <mkd_blockchain.MKDBlockchain object at 0x0000013C9ABCCEE0>
n6 in c0 received MKDBlockchain: <mkd_blockchain.MKDBlockchain object at 0x0000013C9ABCCEE0>
n7 in c0 received MKDBlockchai

In [3]:
#Opens the data set file and generates nodes based on the provided data.
#file is comma delimited in the following format: time-nodeID-xcoor-ycoor-miner-region-prevregion
then = time.time()
with open('node_data.txt') as f:
    lines = f.readlines() # list containing lines of file
    i = 0


    nodes_transacting = []

    for line in lines:
        j = i%num_nodes  # j will represent the increments of nodes
        parts = line.split(',')

        moving_node = nodes[j]  # choosing specific node to manipulate
        # assigning new coordinates to the moving node
        moving_node.coords = [float(parts[2]), float(parts[3])]

        # identifying old and new cluster and calling the move function to perform the needed changes
        old_cluster_id = int(moving_node.cluster_id)
        new_cluster_id = int(parts[5])
        moving_node.move_node(old_cluster_id, new_cluster_id)

        #  generates list of nodes that need to publish a transaction to their cluster
        if int(parts[4]) == 1:
            nodes_transacting.append(moving_node)

        #  Once it reaches the end of num_nodes for each time increment submit transactions
        if j == (num_nodes-1):
            for node in nodes_transacting:
                transaction = SensorTransaction(node.wallet.public_key_string(), random.randint(0,1000))
                node.publish(transaction)

        # if time to forge then forge and broadcast, needs to scan and perform all clusters
            if int(parts[1])%forging_interval == 0:
                for cluster in clusters:
                    #  choose a forger
                    forger = cluster.next_forger()
                    #  if transaction pool not empty then forge and broadcast
                    for node in cluster.member_nodes:
                        if node.wallet.public_key_string() == forger and node.transaction_pool.transactions is not []:
                            node.mkd_forge()
        i += 1

now = time.time() - then
print(f'Complete movement simulation @ {num_nodes} nodes: {now}')



node 1 is about to publish itself
cluster 9 got <node.Node object at 0x0000013C9AAB2DF0>
cluster 9 is handling node <node.Node object at 0x0000013C9AAB2DF0>
cluster 9 got ['-----BEGIN PUBLIC KEY-----\nMIGfMA0GCSqGSIb3DQEBAQUAA4GNADCBiQKBgQCpQ2c9UvIiDOdU4i4yZG0Swyf2\n8ylVMePPSTL0Lqh3Z8gcorYbMLEalUjXPIvuIcdRzjzVUDFt9wWPE4m0InaZH/ul\nUSpEiWpX6zbkrcXsSnVg6v4gHROrYoE0ZkvmuVUAKr/KhXe3S6SN75WQABJG9Ew9\nJhG1hlWvS9TiCqIr6QIDAQAB\n-----END PUBLIC KEY-----', <node.Node object at 0x0000013C9AAB2DF0>]
n1 in c9 received list: ['-----BEGIN PUBLIC KEY-----\nMIGfMA0GCSqGSIb3DQEBAQUAA4GNADCBiQKBgQCpQ2c9UvIiDOdU4i4yZG0Swyf2\n8ylVMePPSTL0Lqh3Z8gcorYbMLEalUjXPIvuIcdRzjzVUDFt9wWPE4m0InaZH/ul\nUSpEiWpX6zbkrcXsSnVg6v4gHROrYoE0ZkvmuVUAKr/KhXe3S6SN75WQABJG9Ew9\nJhG1hlWvS9TiCqIr6QIDAQAB\n-----END PUBLIC KEY-----', <node.Node object at 0x0000013C9AAB2DF0>]
node 2 is about to publish itself
cluster 13 got <node.Node object at 0x0000013C9AB540A0>
cluster 13 is handling node <node.Node object at 0x0000013C9AB540A0>


AttributeError: 'NoneType' object has no attribute 'data'